  Устанавливаю внешний пакет nglview для визуализации структур макромолекул:

In [50]:
!pip install nglview --user

/usr/lib/python3/dist-packages/secretstorage/dhcrypto.py:15: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/usr/lib/python3/dist-packages/secretstorage/util.py:19: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
You should consider upgrading via the '/usr/bin/python3 -m pip install --upgrade pip' command.


Импортирую необходимые модули: для отправки запросов к веб-ресурсам и для работы с форматом json.

In [51]:
import nglview as nv
import requests         
import json             

Формирую запрос по месту поиска, ключевым словам, количеству лигандов, датам публикации записей, разрешению.
Затем вывожу полученный результат - "лучшую находку".

In [52]:
my_query = {
    "query": {
        "type": "group",
        "logical_operator": "and",
        "nodes": []
    },
    "return_type": "entry"
}
keyword_clause = {
    "type": "terminal",
    "service": "full_text", 
    "parameters": {
        "value": "niacin"
    }
}

my_query["query"]["nodes"].append(keyword_clause)

#убрано examle fields search

resolution_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "value": 2.5,
        "attribute": "rcsb_entry_info.resolution_combined",
        "operator": "less_or_equal"
    }
}

has_ligand_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_entry_info.nonpolymer_entity_count",
        "value": 0,
        "operator": "greater"
    }
}

my_query["query"]["nodes"].append(has_ligand_clause)

date_range_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_accession_info.initial_release_date",
        "value": {
            "from": "2020-01-01",
            "to": "2023-01-01",
        },
        "operator": "range"
    }
}

my_query["query"]["nodes"].append(date_range_clause)


rcsb = 'https://search.rcsb.org/rcsbsearch/v1/query'

json_query = json.dumps(my_query) 
search = requests.post(f'{rcsb}', data=json_query)
search
search_result = search.json()
best_hit = search_result["result_set"][0] 
best_hit

{'identifier': '7CV2',
 'score': 1.0,
 'services': [{'service_type': 'full_text',
   'nodes': [{'node_id': 7787,
     'original_score': 14.889928817749023,
     'norm_score': 1.0}]},
  {'service_type': 'text',
   'nodes': [{'node_id': 2725, 'original_score': 1.0, 'norm_score': 1.0},
    {'node_id': 5966, 'original_score': 1.0, 'norm_score': 1.0}]}]}

Загружаю полученную структуру из базы воспользовавшись ее индентификатором.

In [53]:
view = nv.show_pdbid('7cv2') 
view

NGLWidget()

In [54]:
from ipywidgets import interact, fixed

Создам список с отображениями. Каждое отображени записано в виле словаря. Для каждого отображения задаю свои параметры (тип отображения, "что красить", цветовая схема, степень непрозрачности).

In [55]:
my_examples = {
    'Example 1': {
        'description': '''
Поверхность белка покрашена в белый, с непрозрачностью 0.1
Белок представлен в виде rope красного цвета
Боковые радикалы в виде стержневой модели. Окрашены согласно элементу.
Лиганды в виде Ван-дер-Ваальсовых сфер, покрашены по элементам''',
        'representations': [
            {
                'type': 'surface',                      
                'params': {
                    'sele': 'protein',              
                    'color': 'white',
                    'opacity':0.1
                 }
            },
            {
                'type': 'rope',
                'params': {
                    'sele': 'protein',                 
                    'color': 'red'  
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'sidechainAttached',                
                    'color': 'element'  
                 }
            },
            {
                'type': 'spacefill',                      
                'params': {
                    'sele': 'ligand',               
                    'color': 'element'  
                }
            },
        ],
    },

    'Example 2': {
        'description': '''
Белок в виде cartoon, покраска по типу вторичной структуры.
Показана поверхность, с непрозрачностью 0.1
Лиганды в виде hyperball, покрашены в желтый.
''',
        'representations': [
            {
                'type': 'cartoon',                      
                'params': {
                    'sele': 'helix',               
                    'color': 'purple'  
                 }
            },
            {
                'type': 'cartoon',
                'params': {
                    'sele': 'sheet',               
                    'color': 'blue'  
                }
            },
            {
                'type': 'cartoon',
                'params': {
                    'sele': 'turn',                 
                    'color': 'green'  
                 }
            },
            {
                'type': 'surface',                      
                'params': {
                    'sele': 'protein',              
                    'color': 'white',
                    'opacity':0.1
                 }
            },
            {
                'type': 'hyperball',                      
                'params': {
                    'sele': 'ligand',                     
                    'color': 'yellow'  
                 }
            },
        ],
    },
    'Example 3': {
        'description': '''
Белок в виде tube, покраска по типу вторичной структуры.
Боковые радикалы в стержневой модели, покрашены по гидрофобности.
Лиганды в виде линий, покрашены по элементам.
Вода и ионы показаны в виде Ван-дер-Ваальсовых сфер
''',
        'representations': [
            {
                'type': 'tube',
                'params': {
                    'sele': 'helix',               
                    'color': 'purple'  
                 }
            },
            {
                'type': 'tube',
                'params': {
                    'sele': 'sheet',               
                    'color': 'blue'  
                }
            },
             {
                'type': 'tube',
                'params': {
                    'sele': 'turn',                 
                    'color': 'green'  
                 }
            },
             {
                'type': 'licorice',                      
                'params': {
                    'sele': 'sidechainAttached',                
                    'color': 'hydrophobicity'  
                 }
            },
            {
                'type': 'spacefill',                      
                'params': {
                    'sele': 'ion and water',                     
                    'color': 'darkslategray'  
                 }
            },
            {
                'type': 'hyperball',
                'params': {
                    'sele': 'sidechainAttached and basic',                     
                    'color': 'element'  
                }
            },
    ],
    },
}

Создаю интерактивную ячейку, которая позволит просматривать 3 имеющихся отображения:

In [56]:
def show_examples(view, example_name):
    view.clear()
    example = my_examples[example_name]
    print(example['description'])
    view.set_representations(example['representations'])
    view.center()

view = nv.show_pdbid("7cv2", default_representation=False)
interact(show_examples, view=fixed(view), example_name=list(my_examples.keys()))
view

interactive(children=(Dropdown(description='example_name', options=('Example 1', 'Example 2', 'Example 3'), va…

NGLWidget()